# Observing shooting stars


Average time between shooting stars = 15 minutes. What is the probability of seeing 4 stars in one hour?

In [19]:
# Standard data science
import pandas as pd
import numpy as np

%load_ext autoreload
%autoreload 2

# Options for pandas
pd.options.display.max_columns = 20

# Display all cell outputs
from IPython.core.interactiveshell import InteractiveShell
InteractiveShell.ast_node_interactivity = 'all'

# Visualizations
import plotly.plotly as py
import plotly.graph_objs as go
from plotly.offline import iplot

# Cufflinks for dataframes
import cufflinks as cf
cf.go_offline()
cf.set_config_file(world_readable=True, theme='white')

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [20]:
from scipy.special import factorial
import pymc3 as pm

In [54]:
rate = 1/15
minutes = 60
lam = rate * minutes

k = 4
p_k = np.exp(-lam) * np.power(lam, k) / factorial(k)
print(f'The probability of {k} meteors in {minutes} minutes is {p_k:.4f}')

The probability of 4 meteors in 60 minutes is 0.1954


In [96]:
x = np.random.binomial(60, rate, 10000)
(x == 4).mean()

0.1969

In [53]:
p_n

array([0.01376379, 0.05898766, 0.12640212, 0.18057446, 0.19347264,
       0.16583369, 0.11845264, 0.07252202, 0.03885108, 0.01850052])

In [46]:
def calc_prob(lam, k):
     return np.exp(-lam) * np.power(lam, k) / factorial(k)

In [52]:
# Different numbers
ns = np.arange(10)
p_n = calc_prob(lam, ns)

print(f'The most likely value is {np.argmax(p_n) + 1} with probability {np.max(p_n):.4f}')

The most likely value is 5 with probability 0.1935


In [42]:
def plot_line(x, p_x, title=''):
    df = pd.DataFrame({'x': x, 'y': p_x})
    print(f'The most likely value is {np.argmax(p_x) + 1} with probability {np.max(p_x):.4f}')
    df.iplot(kind='scatter', mode='markers+lines', 
             x='x', y='y', xTitle='Number of Events',
             yTitle='Probability', 
            title=title)

In [43]:
plot_line(ns, p_n, title='Probability of Number of Meteors in One Hour')

The most likely value is 3 with probability 0.2240


In [74]:
def plot_lambdas(lams, ns, title=''):
    df = pd.DataFrame()
    for lam in lams:
        df[f'Meteors per Hour = {lam}'] = calc_prob(lam, ns)
    df.index = ns
    df.iplot(kind='scatter', xTitle='Events', yTitle='Probability', title=title)
    return df

In [76]:
df = plot_lambdas(np.array([1/5, 1/10, 1/15, 1/20, 1/30]) * minutes, 
                  list(range(15)), title='Probability of Meteors at Different Rates')

In [81]:
def plot_hist(x, title='',summary=True):
    df = pd.DataFrame(x)
    df.iplot(kind='hist', xTitle='Events', 
             yTitle='Count', title=title)
    if summary:
        print(df.describe())

In [82]:
counts = np.random.poisson(lam, size=10000)
plot_hist(counts, title='Distribution of Number of Meteors in 1 Hour')

                  0
count  10000.000000
mean       3.980800
std        1.987669
min        0.000000
25%        3.000000
50%        4.000000
75%        5.000000
max       12.000000


In [98]:
counts = np.random.poisson(rate * 120, size=10000)
plot_hist(counts, title='Distribution of Number of Meteors in 2 Hour')

                  0
count  10000.000000
mean       8.037800
std        2.830755
min        0.000000
25%        6.000000
50%        8.000000
75%       10.000000
max       22.000000


In [86]:
p_n = calc_prob(lam, np.arange(100))

In [90]:
def pr_less_than_or_equal(p_n, n_query):
    return p_n[:n_query+1].sum() / p_n.sum()

print(f'Probability of 10 or fewer meteors: {pr_less_than_or_equal(p_n, 10):.4f}')

def pr_greater_than(p_n, n_query):
    return 1 - pr_less_than_or_equal(p_n, n_query)

print(f'Probability of more than 4 meteors: {pr_greater_than(p_n, 4):.4f}')

assert pr_less_than_or_equal(p_n, k) + pr_greater_than(p_n, k) == 1

Probability of 10 or fewer meteors: 0.9972
Probability of more than 4 meteors: 0.3712


# Waiting Time

In [92]:
def find_waiting_time(rate, t):
    return np.exp(-rate * t)

t = 15
print(f'Probability of waiting {t} minutes: {find_waiting_time(rate, t):.4f}')

Probability of waiting 15 minutes: 0.3679


In [99]:
ts = np.arange(120)
p_t = find_waiting_time(rate, ts)

In [101]:
p_t.sum()

15.500353609800744

In [104]:
plot_line(ts, p_t / p_t.sum())

The most likely value is 1 with probability 0.0645


In [93]:
def waiting_time_less_than(rate, t):
    return 1 - find_waiting_time(rate, t)

t = 5
print(f'Probability of waiting less than or equal to {t} minutes: {waiting_time_less_than(rate, t):.4f}')

Probability of waiting less than or equal to 5 minutes: 0.2835


# Binomial Versus Poisson Distribution

In [190]:
trials = np.random.binomial(100, rate, size=10000)
trials.mean()

2.6187

In [191]:
trials_poisson = np.random.poisson(rate*spins, size=10000)
trials_poisson.mean()

2.6477

In [195]:
def plot_hist(x, summary=True):
    df = pd.DataFrame(x)
    df.iplot(kind='hist')
    if summary:
        print(df.describe())

In [196]:
plot_hist(trials)

                  0
count  10000.000000
mean       2.618700
std        1.573899
min        0.000000
25%        1.000000
50%        2.000000
75%        4.000000
max       10.000000


In [197]:
plot_hist(trials_poisson)

                  0
count  10000.000000
mean       2.647700
std        1.640016
min        0.000000
25%        1.000000
50%        2.000000
75%        4.000000
max       12.000000


# Distribution

In [180]:
spins = 100
rate = 1/38

def calc_prob_number(rate, number, trials):
    lam = rate * trials
    return np.exp(-lam) * (np.power(lam, number)) / factorial(number)

Expected successes per 1000 spins

In [181]:
lam = rate*spins
lam

2.631578947368421

In [182]:
ns = np.arange(100)
p_n = calc_prob_number(rate, ns, spins)

In [183]:
p_n[ns >= 3].sum()

0.4894689494882201

In [185]:
figure = go.Figure(data=[go.Scatter(x=ns, y=p_n, mode='markers+lines')], layout=go.Layout(xaxis=dict(title='Successes'),
                                                                                         yaxis=dict(title='Density'),
                                                                                         title='Probability Distribution of Number of Successes per 100 Spins'))
iplot(figure)

Try using different rates.

In [ ]:
ra

Alternative using numpy

In [72]:
n = np.random.poisson(lam, size=int(1e4))

df = pd.DataFrame({'n': n})
df['n'].iplot(kind='hist', xTitle='successes / 1000 spins', 
              yTitle='Count', 
              title='Histogram of Successes in 1000 spins for 10000 Trials')

# Waiting Time

In [102]:
ts = np.arange(200)
p_t = np.exp(-rate * ts)

In [103]:
figure = go.Figure(data=[go.Scatter(x=ts, y=p_t / p_t.sum(), mode='markers+lines')], layout=go.Layout(xaxis=dict(title='Waiting Time (spins)'),
                                                                                         yaxis=dict(title='Density'),
                                                                                         title='Probability Distribution of Waiting Time'))
iplot(figure)

In [86]:
np.argmax(ts * p_t)

36

Probability of waiting more than 100 spins.

In [97]:
np.exp(-rate * 100)

0.06217652402211632

In [100]:
from math import pow, exp, factorial

class Exponential:

    def __init__(self, rate):
        self.rate = rate

    def prob_less_than_or_equal(self, t):
        rate = self.rate * t
        return 1 - exp(-rate)

    def prob_greater_than(self, t):
        return 1 - self.prob_less_than_or_equal(t)

    def prob_between(self, t1, t2):
        p1 = self.prob_less_than_or_equal(t1)
        p2 = self.prob_less_than_or_equal(t2)

        return p2 - p1

expo = Exponential(1/38)
print(expo.prob_greater_than(100))
print(expo.prob_less_than_or_equal(100))
print(expo.prob_between(50, 150))

0.062176524022116375
0.9378234759778836
0.23384835517828695


# Arrivals

In [102]:
rand.rand(2)

array([0.63641041, 0.31435598])

In [113]:
spins = 10000
time_between = 36  

rand = np.random.RandomState(42)
success_times = spins * time_between * np.sort(rand.rand(spins))

In [115]:
waiting_times = np.diff(success_times)

df = pd.DataFrame({'waiting_time': waiting_times})
df['waiting_time'].iplot(kind='hist', xTitle='Waiting Time', 
              yTitle='Count', bins=(0, 400, 10),
              title='Histogram of Waiting Times')

In [116]:
np.mean(waiting_times)

35.9930166887764

# Visualizing Successes

In [158]:
spins = np.random.choice([0, 1], size = 100, replace=True, p=[1-rate, rate])
success_times = np.where(spins==1)[0]
waiting_times = np.diff(np.where(spins == 1))
waiting_times[:10]

array([[68,  2, 10, 10]])

In [159]:
annotations = [go.layout.Annotation(x=x, y=1, text=str(x), ax=0, ay=200) for x in success_times]

In [160]:
figure = go.Figure(data=[go.Scatter(x=success_times, y=np.ones(shape=len(success_times)), mode='markers')], 
                   layout=go.Layout(annotations=annotations, yaxis=dict(range=(0, 1))))
iplot(figure)

In [134]:
annotations

[layout.Annotation({
     'text': ('[ 66 136 157 201 222 269 290 3' ... '6 866 890 951 954 970 971 980]'),
     'x': array([ 66, 136, 157, 201, 222, 269, 290, 326, 348, 457, 484, 523, 526, 552,
                 571, 663, 671, 673, 687, 743, 751, 856, 866, 890, 951, 954, 970, 971,
                 980]),
     'y': 1
 })]